# IBM week 4 Applied Data science Capstone
### The battle of Neighborhoods

Introduction where you discuss the business problem and who would be interested in this project.

"Would you recommend a location in Germany to open a Restaurant ?"


My team leader wants me to concentrated on selection of good location according to its nearby environment. she lists mostly rated and top 10 restaurants.

I work with my teammates and select 5 possible locations to build the Restaurant. Which location should be suggested to them?



In [114]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

!conda install -c conda-forge geocoder --yes
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print("Libraries imported.")

Solving environment: ...working... 
  - anaconda/win-64::openssl-1.1.1d-he774522_2
  - defaults/win-64::openssl-1.1.1d-he774522_2done

# All requested packages already installed.

Solving environment: ...working... 
  - anaconda/win-64::openssl-1.1.1d-he774522_2
  - defaults/win-64::openssl-1.1.1d-he774522_2done

# All requested packages already installed.

Libraries imported.


In [115]:
df = pd.read_csv("Zipcodes.de.csv",error_bad_lines=False)
df.head()

country_code  zipcode        place        state state_code province  \
0           DE     1945    Grünewald  Brandenburg         BB      NaN   
1           DE     1945     Lindenau  Brandenburg         BB      NaN   
2           DE     1945   Hohenbocka  Brandenburg         BB      NaN   
3           DE     1945  Schwarzbach  Brandenburg         BB      NaN   
4           DE     1945     Guteborn  Brandenburg         BB      NaN   

   province_code                        community  community_code  latitude  \
0              0  Landkreis Oberspreewald-Lausitz           12066   51.4000   
1              0  Landkreis Oberspreewald-Lausitz           12066   51.4000   
2              0  Landkreis Oberspreewald-Lausitz           12066   51.4310   
3              0  Landkreis Oberspreewald-Lausitz           12066   51.4500   
4              0  Landkreis Oberspreewald-Lausitz           12066   51.4167   

   longitude  
0    14.0000  
1    13.7333  
2    14.0098  
3    13.9333  
4    13.9333

In [116]:
Germany = df.drop(['country_code','state_code','province','province_code','community','community_code'],axis=1)

In [117]:
Germany

zipcode                                              place  \
0         1945                                          Grünewald   
1         1945                                           Lindenau   
2         1945                                         Hohenbocka   
3         1945                                        Schwarzbach   
4         1945                                           Guteborn   
5         1945                                          Hermsdorf   
6         1945                                            Ruhland   
7         1945                                             Tettau   
8         1945                                            Kroppen   
9         1968                                   Schipkau Hörlitz   
10        1968                                        Senftenberg   
11        1968                                           Schipkau   
12        1979                                        Lauchhammer   
13        1983                                        Neu-Seeland   
14        1983                                        Großräschen   
15        1987                                       Schwarzheide   
16        1990                                            Ortrand   
17        1990                                        Großkmehlen   
18        1990                                         Frauendorf   
19        1993                                  Schipkau Schipkau   
20        1993                                           Schipkau   
21        1994                      Schipkau Annahütte, Annahütte   
22        1994             Schipkau Annahütte, Karl-Marx-Siedlung   
23        1994                                   Schipkau Drochow   
24        1994                                           Schipkau   
25        1994                                     Schipkau Meuro   
26        1994                                 Schipkau Annahütte   
27        1994             Schipkau Annahütte, Annahütte-Siedlung   
28        1994                    Schipkau Annahütte, Herrnnmühle   
29        1996                                             Hosena   
30        1998                                           Schipkau   
31        1998                                     Schipkau Meuro   
32        1998                                 Schipkau Klettwitz   
33        3042                                            Cottbus   
34        3044                                            Cottbus   
35        3046                                            Cottbus   
36        3048                                            Cottbus   
37        3050                                            Cottbus   
38        3051                                            Cottbus   
39        3052                                            Cottbus   
40        3053                                            Cottbus   
41        3054                                            Cottbus   
42        3055                                            Cottbus   
43        3058                                         Groß Oßnig   
44        3058                                       Groß Döbbern   
45        3058                                             Haasow   
46        3058                                      Klein Döbbern   
47        3058                                          Neuhausen   
48        3058                                            Kathlow   
49        3058                                             Sergen   
50        3058                                            Koppatz   
51        3058                                            Gablenz   
52        3058                                        Groß Gaglow   
53        3058                                         Frauendorf   
54        3058                                         Kiekebusch   
55        3058                                           Roggosen   
56        3058                                        Komptendorf   
57   

In [118]:
# Retrieve the Latitude and Longitude for Paris
from geopy.geocoders import Nominatim 

address = 'Germany'

# Define the user_agent as Paris_explorer
geolocator = Nominatim(user_agent="Germany_explorer")

location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geographical coordinates of Germany are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Germany are 51.0834196, 10.4234469.


In [119]:
print('The dataframe has {} state and {} places.'.format(
        len(Germany['state'].unique()),
        Germany.shape[0]
    )
)

The dataframe has 16 state and 16481 places.


In [120]:
#count Bourough and Neighborhood
Germany.groupby('state').count()['place']

state
Baden-Württemberg         1387
Bayern                    2259
Berlin                     195
Brandenburg               1287
Bremen                      41
Hamburg                    396
Hessen                     572
Mecklenburg-Vorpommern    1015
Niedersachsen             1750
Nordrhein-Westfalen        895
Rheinland-Pfalz           2356
Saarland                    69
Sachsen                    689
Sachsen-Anhalt            1338
Schleswig-Holstein        1189
Thüringen                 1043
Name: place, dtype: int64

In [121]:
#Berlin = Germany.loc[Germany['state']=='Brandenburg']
#Berlin

In [122]:
df_Bremen = Germany[Germany['state'].str.contains('Bremen')]
df_Bremen.reset_index(inplace=True)
df_Bremen.drop('index', axis=1, inplace=True)
df_Bremen = df_Bremen.head(9)

C:\Users\hp\Anaconda3\lib\site-packages\pandas\core\frame.py:4102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [123]:
df_saar = Germany[Germany['state'].str.contains('Saarland')]
df_saar.reset_index(inplace=True)
df_saar.drop('index', axis=1, inplace=True)
df_saar = df_saar.head(9)

In [124]:
df_hessen = Germany[Germany['state'].str.contains('Hessen')]
df_hessen.reset_index(inplace=True)
df_hessen.drop('index', axis=1, inplace=True)
df_hessen = df_hessen.head(7)

In [125]:
df_rhein = Germany[Germany['state'].str.contains('Rheinland-Pfalz')]
df_rhein.reset_index(inplace=True)
df_rhein.drop('index', axis=1, inplace=True)
df_rhein = df_rhein.head(17)

In [126]:
df_west = pd.concat([df_Bremen, df_saar, df_hessen, df_rhein])
df_west

zipcode                   place            state  latitude  longitude
0     27568             Bremerhaven           Bremen   53.5687     8.5741
1     27570             Bremerhaven           Bremen   53.5286     8.5907
2     27572             Bremerhaven           Bremen   53.5002     8.6047
3     27574             Bremerhaven           Bremen   53.5299     8.6098
4     27576             Bremerhaven           Bremen   53.5545     8.5933
5     27578             Bremerhaven           Bremen   53.5887     8.5977
6     27580             Bremerhaven           Bremen   53.5685     8.5968
7     28195                  Bremen           Bremen   53.0889     8.7906
8     28197                  Bremen           Bremen   53.0854     8.7463
0     66111             Saarbrücken         Saarland   49.2461     7.0022
1     66113             Saarbrücken         Saarland   49.2431     6.9757
2     66115             Saarbrücken         Saarland   49.2399     6.9696
3     66117             Saarbrücken         Saarland   49.2146     6.9682
4     66119             Saarbrücken         Saarland   49.2087     7.0202
5     66121             Saarbrücken         Saarland   49.2290     7.0124
6     66123             Saarbrücken         Saarland   49.2333     7.0000
7     66125             Saarbrücken         Saarland   49.2718     7.0325
8     66126             Saarbrücken         Saarland   49.2333     7.0000
0     35510                Butzbach           Hessen   50.4339     8.6712
1     35516              Münzenberg           Hessen   50.4563     8.7293
2     35519              Rockenberg           Hessen   50.4305     8.7369
3     36381             Schlüchtern           Hessen   50.3655     9.5829
4     36391                 Sinntal           Hessen   50.3127     9.6234
5     36396   Steinau an der Straße           Hessen   50.3140     9.4633
6     55246          Mainz-Kostheim           Hessen   50.0051     8.3134
0     51598            Friesenhagen  Rheinland-Pfalz   50.9038     7.8096
1     53424                 Remagen  Rheinland-Pfalz   50.5788     7.2270
2     53426              Königsfeld  Rheinland-Pfalz   50.4979     7.1771
3     53426               Dedenbach  Rheinland-Pfalz   50.4833     7.1833
4     53426            Schalkenbach  Rheinland-Pfalz   50.4949     7.1464
5     53474  Bad Neuenahr-Ahrweiler  Rheinland-Pfalz   50.5432     7.1113
6     53489                  Sinzig  Rheinland-Pfalz   50.5438     7.2464
7     53498             Bad Breisig  Rheinland-Pfalz   50.5052     7.2886
8     53498                 Waldorf  Rheinland-Pfalz   50.4833     7.2333
9     53498             Gönnersdorf  Rheinland-Pfalz   50.4833     7.2667
10    53501              Grafschaft  Rheinland-Pfalz   50.5833     7.0667
11    53505               Kirchsahr  Rheinland-Pfalz   50.5225     6.8998
12    53505                Altenahr  Rheinland-Pfalz   50.5169     6.9921
13    53505               Kalenborn  Rheinland-Pfalz   50.5500     7.0000
14    53505                    Berg  Rheinland-Pfalz   50.5552     6.9489
15    53506                    Lind  Rheinland-Pfalz   50.5000     6.9333
16    53506                    Rech  Rheinland-Pfalz   50.5167     7.0333

In [153]:
# create map of Paris using the above latitude and longitude values
map_Germany = folium.Map(location=[latitude, longitude], zoom_start=12)


# add markers to map
for lat, lng, label in zip(Germany['latitude'], Germany['longitude'], Germany['place']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=25,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.3,
        parse_html=False).add_to(map_Berlin)  
    
#map_Germany

In [128]:
#Create list with the Boroughs (to be used later)
boroughs = df_west['state'].unique().tolist()

In [129]:
lat_west = df_west['latitude'].mean()
lon_west = df_west['longitude'].mean()
print('The geographical coordinates of west Germany are {}, {}'.format(lat_west, lon_west))

The geographical coordinates of west Germany are 50.85031666666667, 7.746880952380952


In [130]:
borough_color = {}
for borough in boroughs:
    borough_color[borough]= '#%02X%02X%02X' % tuple(np.random.choice(range(256), size=3)) #Random color

In [131]:
CLIENT_ID = 'ZAIQQPOTCED3QTSSNSVGI5U2JPUK2AL4JDZOZ1L2EF4CER0E'

CLIENT_SECRET = 'YG2WLQBP2F0W3J3KSVOCP2USPHNB3M3WCBOMOBUZ25AGKEFN'

VERSION = '20180605' # Foursquare API version

In [132]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [133]:
#Get venues for all neighborhoods in our dataset
west_venues = getNearbyVenues(names=df_west['place'],
                                latitudes=df_west['latitude'],
                                longitudes=df_west['longitude'])

Bremerhaven
Bremerhaven
Bremerhaven
Bremerhaven
Bremerhaven
Bremerhaven
Bremerhaven
Bremen
Bremen
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Saarbrücken
Butzbach
Münzenberg
Rockenberg
Schlüchtern
Sinntal
Steinau an der Straße
Mainz-Kostheim
Friesenhagen
Remagen
Königsfeld
Dedenbach
Schalkenbach
Bad Neuenahr-Ahrweiler
Sinzig
Bad Breisig
Waldorf
Gönnersdorf
Grafschaft
Kirchsahr
Altenahr
Kalenborn
Berg
Lind
Rech


In [134]:
west_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Bremerhaven                53.5286                  8.5907   
1  Bremerhaven                53.5286                  8.5907   
2  Bremerhaven                53.5286                  8.5907   
3  Bremerhaven                53.5286                  8.5907   
4  Bremerhaven                53.5286                  8.5907   

                     Venue  Venue Latitude  Venue Longitude  Venue Category  
0             Eis-Café Teo       53.529981         8.592467  Ice Cream Shop  
1  Wochenmarkt Geestemünde       53.531341         8.591685  Farmers Market  
2                 E center       53.526183         8.594978     Supermarket  
3                     Lidl       53.526196         8.593942     Supermarket  
4                 Rossmann       53.532411         8.593789       Drugstore

In [135]:
west_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                   
Altenahr                                    7                       7      7   
Bad Breisig                                 3                       3      3   
Bad Neuenahr-Ahrweiler                     14                      14     14   
Berg                                        1                       1      1   
Bremen                                      9                       9      9   
Bremerhaven                                30                      30     30   
Butzbach                                   10                      10     10   
Friesenhagen                                1                       1      1   
Grafschaft                                  1                       1      1   
Kalenborn                                   3                       3      3   
Kirchsahr                                   1                       1      1   
Königsfeld                                  4                       4      4   
Mainz-Kostheim                              1                       1      1   
Münzenberg                                  4                       4      4   
Rech                                        7                       7      7   
Remagen                                     8                       8      8   
Rockenberg                                  1                       1      1   
Saarbrücken                               203                     203    203   
Schalkenbach                                2                       2      2   
Sinntal                                     5                       5      5   
Sinzig                                      6                       6      6   
Steinau an der Straße                       4                       4      4   
Waldorf                                     1                       1      1   

                        Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                             
Altenahr                             7                7               7  
Bad Breisig                          3                3               3  
Bad Neuenahr-Ahrweiler              14               14              14  
Berg                                 1                1               1  
Bremen                               9                9               9  
Bremerhaven                         30               30              30  
Butzbach                            10               10              10  
Friesenhagen                         1                1               1  
Grafschaft                           1                1               1  
Kalenborn                            3                3               3  
Kirchsahr                            1                1               1  
Königsfeld                           4                4               4  
Mainz-Kostheim                       1                1               1  
Münzenberg                           4                4               4  
Rech                                 7                7               7  
Remagen                              8                8               8  
Rockenberg                           1                1               1  
Saarbrücken                        203              203             203  
Schalkenbach                         2                2               2  
Sinntal                              5                5               5  
Sinzig                               6                6               6  
Steinau an der Straße                4                4               4  
Waldorf                              1                1               1

In [136]:
#Number of unique venue categories
print('There are {} uniques categories.'.format(len(west_venues['Venue Category'].unique())))
#print out the list of categories
west_venues['Venue Category'].unique()[:100]

There are 106 uniques categories.


array(['Ice Cream Shop', 'Farmers Market', 'Supermarket', 'Drugstore',
       'Fast Food Restaurant', 'Plaza', 'Business Service',
       'Churrascaria', 'Paper / Office Supplies Store', 'Grocery Store',
       'Gas Station', 'Bus Stop', 'Hockey Rink', 'Concert Hall',
       'Hardware Store', 'Hotel', 'Basketball Stadium', 'Sandwich Place',
       'Pizza Place', 'Modern European Restaurant', 'Big Box Store',
       'Train Station', 'Smoke Shop', 'German Restaurant', 'Tram Station',
       'Italian Restaurant', 'Soccer Field', 'Liquor Store', 'Nightclub',
       'Bus Station', 'Pet Store', 'Light Rail Station',
       'Falafel Restaurant', 'Bowling Alley', 'Athletics & Sports',
       'Tennis Court', 'Automotive Shop', 'Fried Chicken Joint', 'Café',
       'Pastry Shop', 'French Restaurant', 'Steakhouse',
       'Thai Restaurant', 'Currywurst Joint', 'Sushi Restaurant', 'Pub',
       'Creperie', 'Vegetarian / Vegan Restaurant', 'Bakery', 'Bar',
       'Indonesian Restaurant', 'Movie The

In [137]:
# check if the results contain "Thai Restaurants"
#please note I changed the data to Thai because I was previously writing the code using Asian but the number is so small
"Indie Movie Theater" in west_venues['Venue Category'].unique()

True

In [138]:
# one hot encoding
to_onehot = pd.get_dummies(west_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = west_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(326, 107)


Neighborhoods  American Restaurant  Asian Restaurant  Athletics & Sports  \
0   Bremerhaven                    0                 0                   0   
1   Bremerhaven                    0                 0                   0   
2   Bremerhaven                    0                 0                   0   
3   Bremerhaven                    0                 0                   0   
4   Bremerhaven                    0                 0                   0   

   Automotive Shop  BBQ Joint  Bakery  Bank  Bar  Basketball Stadium  \
0                0          0       0     0    0                   0   
1                0          0       0     0    0                   0   
2                0          0       0     0    0                   0   
3                0          0       0     0    0                   0   
4                0          0       0     0    0                   0   

   Beer Garden  Big Box Store  Bistro  Boarding House  Bowling Alley  \
0            0              0       0               0              0   
1            0              0       0               0              0   
2            0              0       0               0              0   
3            0              0       0               0              0   
4            0              0       0               0              0   

   Breakfast Spot  Burger Joint  Bus Station  Bus Stop  Business Service  \
0               0             0            0         0                 0   
1               0             0            0         0                 0   
2               0             0            0         0                 0   
3               0             0            0         0                 0   
4               0             0            0         0                 0   

   Café  Castle  Cheese Shop  Church  Churrascaria  Clothing Store  \
0     0       0            0       0             0               0   
1     0       0            0       0             0               0   
2     0       0            0       0             0               0   
3     0       0            0       0             0               0   
4     0       0            0       0             0               0   

   Cocktail Bar  Coffee Shop  Concert Hall  Creperie  Currywurst Joint  \
0             0            0             0         0                 0   
1             0            0             0         0                 0   
2             0            0             0         0                 0   
3             0            0             0         0                 0   
4             0            0             0         0                 0   

   Department Store  Doner Restaurant  Drugstore  Entertainment Service  \
0                 0                 0          0                      0   
1                 0                 0          0                      0   
2                 0                 0          0                      0   
3                 0                 0          0                      0   
4                 0                 0          1                      0   

   Falafel Restaurant  Farmers Market  Fast Food Restaurant  Flower Shop  \
0                   0               0                     0            0   
1                   0               1                     0            0   
2                   0               0                     0            0   
3                   0               0                     0            0   
4                   0               0                     0            0   

   Fountain  French Restaurant  Fried Chicken Joint  Gas Station  Gastropub  \
0         0                  0                    0            0          0   
1         0                  0                    0            0          0   
2         0                  0                    0            0          0   
3         0                  0                    0            0          0   
4         0                  0           

In [139]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(23, 107)


Neighborhoods  American Restaurant  Asian Restaurant  \
0                 Altenahr             0.000000          0.000000   
1              Bad Breisig             0.000000          0.000000   
2   Bad Neuenahr-Ahrweiler             0.000000          0.000000   
3                     Berg             0.000000          0.000000   
4                   Bremen             0.000000          0.000000   
5              Bremerhaven             0.000000          0.000000   
6                 Butzbach             0.000000          0.000000   
7             Friesenhagen             0.000000          0.000000   
8               Grafschaft             0.000000          0.000000   
9                Kalenborn             0.000000          0.000000   
10               Kirchsahr             0.000000          0.000000   
11              Königsfeld             0.000000          0.000000   
12          Mainz-Kostheim             0.000000          0.000000   
13              Münzenberg             0.000000          0.000000   
14                    Rech             0.000000          0.000000   
15                 Remagen             0.000000          0.000000   
16              Rockenberg             0.000000          0.000000   
17             Saarbrücken             0.009852          0.000000   
18            Schalkenbach             0.000000          0.000000   
19                 Sinntal             0.000000          0.000000   
20                  Sinzig             0.000000          0.166667   
21   Steinau an der Straße             0.000000          0.000000   
22                 Waldorf             0.000000          0.000000   

    Athletics & Sports  Automotive Shop  BBQ Joint    Bakery  Bank       Bar  \
0             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
1             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
2             0.000000         0.000000   0.071429  0.000000  0.00  0.000000   
3             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
4             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
5             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
6             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
7             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
8             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
9             0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
10            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
11            0.000000         0.000000   0.000000  0.000000  0.25  0.000000   
12            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
13            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
14            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
15            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
16            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
17            0.009852         0.004926   0.000000  0.024631  0.00  0.068966   
18            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
19            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
20            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
21            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   
22            0.000000         0.000000   0.000000  0.000000  0.00  0.000000   

    Basketball Stadium  Beer Garden  Big Box Store    Bistro  Boarding House  \
0             0.000000     0.000000       0.000000  0.000000        0.000000   
1             0.000000     0.000000       0.000000  0.000000        0.333333   
2             0.000000     0.000000       0.000000  0.000000        0.000000   
3             0.000000     0.000000       0.000000  0.000000        0.000000   
4             0.000000     0.000000

In [140]:
len(to_grouped[to_grouped["Fast Food Restaurant"] > 0])

3

In [141]:
to_asian = to_grouped[["Neighborhoods","Fast Food Restaurant"]]
to_asian.head()

Neighborhoods  Fast Food Restaurant
0                Altenahr              0.000000
1             Bad Breisig              0.000000
2  Bad Neuenahr-Ahrweiler              0.071429
3                    Berg              0.000000
4                  Bremen              0.000000

## Cluster Neighbourhoods

In [142]:
# set number of clusters
toclusters = 3

to_clustering = to_asian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 2, 0, 0, 1, 1, 0, 0, 0])

In [143]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = to_asian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [144]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  Fast Food Restaurant  Cluster Labels
0                Altenahr              0.000000               0
1             Bad Breisig              0.000000               0
2  Bad Neuenahr-Ahrweiler              0.071429               2
3                    Berg              0.000000               0
4                  Bremen              0.000000               0

In [145]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(west_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(326, 9)


Neighborhood  Fast Food Restaurant  Cluster Labels  Neighborhood Latitude  \
0     Altenahr                   0.0               0                50.5169   
0     Altenahr                   0.0               0                50.5169   
0     Altenahr                   0.0               0                50.5169   
0     Altenahr                   0.0               0                50.5169   
0     Altenahr                   0.0               0                50.5169   

   Neighborhood Longitude                                   Venue  \
0                  6.9921                                Burg Are   
0                  6.9921                            Hotel Ruland   
0                  6.9921                 Haus Caspari (Altenahr)   
0                  6.9921                          Hotel Zur Post   
0                  6.9921  Hotel & Restaurant Zum Schwarzen Kreuz   

   Venue Latitude  Venue Longitude Venue Category  
0       50.517554         6.995131         Castle  
0       50.516430         6.990832     Restaurant  
0       50.517050         6.992264           Café  
0       50.516467         6.989753          Hotel  
0       50.516076         6.989864          Hotel

In [146]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(326, 9)


Neighborhood  Fast Food Restaurant  Cluster Labels  \
0                 Altenahr              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17             Saarbrücken              0.000000               0   
17

In [147]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [148]:
map_clusters = folium.Map(location=[lat_west, lon_west], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
#map_clusters

In [149]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

## Examine Clusters

In [150]:
#Cluster 0
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  Fast Food Restaurant  Cluster Labels  \
0                Altenahr                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0               0   
17            Saarbrücken                   0.0             

In [151]:
#Cluster 1
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Fast Food Restaurant  Cluster Labels  Neighborhood Latitude  \
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5002   
5  Bremerhaven                   0.1               1                53.5286   
5  Bremerhaven                   0.1               1                53.5002   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
6     Butzbach                   0.1               1                50.4339   
5  Bremerhaven                   0.1               1                53.5002   
6     Butzbach                   0.1               1                50.4339   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5545   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5685   
5  Bremerhaven                   0.1               1                53.5002   
5  Bremerhaven                   0.1               1                53.5299   
5  Bremerhaven                   0.1               1                53.5887   
5  Bremerhaven                   0.1               1                53.5299   
5  Bremerhaven                   0.1               1                53.5545   
5  Bremerhaven                   0.1               1                53.5545   
5  Bremerhaven                   0.1               1                53.5545   
5  Bremerhaven                   0.1               1                53.5545   
5  Bremerhaven                   0.1               1                53.5887   
5  Bremerhaven                   0.1               1                53.5887   
5  Bremerhaven                   0.1               1                53.5685   

   Neighborhood Longitude                            Venue  Venue Latitude  \
5                  8.5907  EDEKA Center Georg-Seebeck-Str.       53.525910   
5                  8.5907            Konrad-Adenauer-Platz       53.532049   
5                  8.5907                         Rossmann       53.532411   
5                  8.5907                     Eis-Café Teo       53.529981   
5                  8.5907                         E center       53.526183   
5                  8.5907          Wochenmarkt Geestemünde       53.531341   
5                  8.5907            Netto Marken-Discount       53.529891   
5                  8.5907                             Lidl       53.526196   
5                  8.6047   Planungsbüro Stefan Heise GmbH  

In [152]:
#Cluster 2
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood  Fast Food Restaurant  Cluster Labels  \
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   
2  Bad Neuenahr-Ahrweiler              0.071429               2   

   Neighborhood Latitude  Neighborhood Longitude  \
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   
2                50.5432                  7.1113   

                                   Venue  Venue Latitude  Venue Longitude  \
2              Schlemmer Grill Ahrweiler       50.545454         7.107265   
2                                   Aral       50.545611         7.112036   
2                                Knauber       50.546841         7.111141   
2                                   Lidl       50.546678         7.113873   
2                              HIT-Markt       50.545821         7.109860   
2                      Bahnhof Ahrweiler       50.546681         7.109013   
2                              Fressnapf       50.544233         7.108534   
2                              Deichmann       50.544978         7.108940   
2  Jugendherberge Bad Neuenahr-Ahrweiler       50.541619         7.114724   
2                        Spielzeug Fritz       50.545666         7.109412   
2                               ALDI SÜD       50.545990         7.106322   
2                             McDonald's       50.546238         7.110233   
2                      dm-drogerie markt       50.546316         7.111385   
2                    Intersport Krumholz       50.546303         7.108446   

         Venue Category  
2             BBQ Joint  
2           Gas Station  
2        Hardware Store  
2           Supermarket  
2           Supermarket  
2         Train Station  
2             Pet Store  
2            Shoe Store  
2                Hostel  
2      Toy / Game Store  
2           Supermarket  
2  Fast Food Restaurant  
2             Drugstore  
2   Sporting Goods Shop

Observations
Most of Thai restaurants are in Cluster 2 which is around Bad Neuenhr Ahrweiler, Bremerhaven areas and lowest (close to zero) in Cluster 1 areas which are Butzbach areas. Also, there are good opportunities to open near la pizza, italian restuarant as the competition seems to be low. Looking at nearby venues, it seems Cluster 1 might be a good location as there are not a lot of Asian restaurants in these areas. Therefore, this project recommends the entrepreneur to open an authentic Burmese restaurant in these locations with little to no competition. Nonetheless, if the food is authentic, affordable and good taste, I am confident that it will have great following everywhere =)